# Capstone Project - The Battle of Neighborhoods
# Finding the Best Neighborhood in New York

## Introduction:
Recently, one of my client has approached me to find out the most suitable place in New York to live.
He wants to move to the most happening place in New York.
### Business Problem
Given that there are many neighbourhoods in New York
Exploring the neighbouhoods 
Using the Foursquare API to analyse 
Find the most sought after, trendy, popular and commented venues. 

## Importing Necessary Libraries

In [ ]:
import pandas as pd
import numpy as np
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library


# Data Collection
## Web Scrapping with BeautifulSoup

In [ ]:
from bs4 import BeautifulSoup
import requests
import re

url = "https://www.google.com/search?q=new+york+neighbourhoods&oq=new+york+neighbourhoods&aqs=chrome..69i57j0l7.12674j0j7&sourceid=chrome&ie=UTF-8"
response = requests.get(url)
NY_data = BeautifulSoup(response.text, 'lxml')
contents=NY_data.find_all('div', class_='RWuggc kCrYT')
columns = ['Neighborhood']
NY_neighborhood = pd.DataFrame(columns = columns)
for content in contents:
    #coordinate = content.find('div', class_='BNeawe s3v9rd AP7Wnd')
    neighbor_ = content.find('div').find('div').text
    NY_neighborhood = NY_neighborhood.append({'Neighborhood': neighbor_}, ignore_index=True)
NY_neighborhood


Neighborhood
0      Midtown Manhattan
1                   SoHo
2                 Harlem
3        Upper East Side
4                Tribeca
5        Upper West Side
6           Williamsburg
7        Lower East Side
8        Lower Manhattan
9      Greenwich Village
10          East Village
11          Little Italy
12    Financial District
13             Chinatown
14        Hell's Kitchen
15                 Dumbo
16               Chelsea
17     Flatiron District
18               Astoria
19            Park Slope
20                Nolita
21         Gramercy Park
22            Greenpoint
23      Long Island City
24  Meatpacking District
25      Brooklyn Heights
26          Midtown East
27      Theater District
28           Murray Hill
29    Washington Heights
30          West Village
31          Union Square
32              Bushwick
33     Battery Park City
34    Bedford-Stuyvesant
35           East Harlem
36              Flushing
37      Prospect Heights
38                Inwood
39       Carroll Gardens
40       Jackson Heights
41           Fort Greene
42             Bay Ridge
43           Boerum Hill
44              Red Hook
45           Sunset Park
46      Garment District
47           Cobble Hill
48       Upper Manhattan
49   Morningside Heights
50         Crown Heights
51              Flushing
52               Astoria
53      Long Island City
54          Forest Hills

## Defining a funtion to get the new york city data such as Boroughs Neighborhoods along with their Latitude and Longitude.



In [ ]:
NY_coord = pd.DataFrame(columns = ['Latitude','Longitude'])
geolocator = Nominatim(user_agent="New York")
for row in NY_neighborhood['Neighborhood']:
    location = geolocator.geocode(row)
    NY_coord = NY_coord.append({'Latitude':location.latitude, 'Longitude':location.longitude}, ignore_index=True)
NY_neighborhood = NY_neighborhood.join(NY_coord)
NY_neighborhood

Neighborhood   Latitude   Longitude
0      Midtown Manhattan  40.760109  -73.978163
1                   SoHo  51.513163   -0.131175
2                 Harlem  40.807879  -73.945415
3        Upper East Side  40.773702  -73.964120
4                Tribeca  40.715380  -74.009306
5        Upper West Side  40.787045  -73.975416
6           Williamsburg  37.278921  -76.694486
7        Lower East Side  40.715936  -73.986806
8        Lower Manhattan  51.113231   17.018655
9      Greenwich Village  40.733584  -74.002817
10          East Village  40.729269  -73.987361
11          Little Italy  40.719273  -73.998215
12    Financial District  40.707612  -74.009378
13             Chinatown  40.716491  -73.996250
14        Hell's Kitchen  40.764423  -73.992392
15                 Dumbo  40.702905  -73.990117
16               Chelsea  51.487542   -0.168220
17     Flatiron District  40.741072  -73.989653
18               Astoria  46.187885 -123.831256
19            Park Slope  40.670103  -73.985972
20                Nolita  53.342452   -6.264777
21         Gramercy Park  40.737925  -73.985932
22            Greenpoint  40.723713  -73.950971
23      Long Island City  40.741509  -73.956975
24  Meatpacking District  40.740803  -74.008069
25      Brooklyn Heights  40.696085  -73.995028
26          Midtown East  40.759822  -73.972471
27      Theater District  40.757980  -73.985545
28           Murray Hill  38.290348  -85.588294
29    Washington Heights  40.840198  -73.940221
30          West Village  40.734186  -74.005580
31          Union Square  40.735909  -73.990163
32              Bushwick  40.694270  -73.918748
33     Battery Park City  40.711017  -74.016937
34    Bedford-Stuyvesant  40.683436  -73.941249
35           East Harlem  40.794722  -73.942500
36              Flushing  40.765430  -73.817429
37      Prospect Heights  42.095305  -87.937569
38                Inwood  43.307926  -96.432184
39       Carroll Gardens  40.678420  -73.994802
40       Jackson Heights  40.755656  -73.885775
41           Fort Greene  40.690771  -73.976624
42             Bay Ridge  40.633993  -74.014584
43           Boerum Hill  40.685626  -73.984171
44              Red Hook  40.675103  -74.009584
45           Sunset Park  40.644337  -74.007532
46      Garment District  40.753694  -73.990517
47           Cobble Hill  40.687500  -73.998056
48       Upper Manhattan  46.193819    6.230278
49   Morningside Heights  40.810000  -73.962500
50         Crown Heights  40.667471  -73.943566
51              Flushing  40.765430  -73.817429
52               Astoria  46.187885 -123.831256
53      Long Island City  40.741509  -73.956975
54          Forest Hills  38.215348  -85.585793

### Plotting the map with Folium

In [ ]:
address = 'New York'

geolocator = Nominatim(user_agent="New York")
location = geolocator.geocode(address)
latitude_NY = location.latitude
longitude_NY = location.longitude
map_NY = folium.Map(location=[latitude_NY, longitude_NY], zoom_start=12)

# add markers to map
for lat, lng, postal in zip(NY_neighborhood['Latitude'],NY_neighborhood['Longitude'],NY_neighborhood['Neighborhood']):
    label = str(postal)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [float(lat), float(lng)],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_NY)  
    
map_NY

## Getting Venues List via FourSquare API

In [ ]:
CLIENT_ID = 'ILLMWN3IEHII4JAWIVV13BLYXJ31QCGQ23FL2KG552DNEFPD' #Foursquare ID
CLIENT_SECRET ='BXPXXEIO4AUTWA2IJDFFTY1JGLJYIWO4GPCSSSRVQBFAYOP1'
VERSION = '20180605' # Foursquare API version

radius=5000
LIMIT=100
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        print(results)
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)
NY_venues = getNearbyVenues(names=NY_neighborhood['Neighborhood'],
                                   latitudes=NY_neighborhood['Latitude'],
                                   longitudes=NY_neighborhood['Longitude']
                                  )


[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4161e400f964a520721d1fe3', 'name': 'Radio City Music Hall', 'location': {'address': '1260 Avenue of the Americas', 'crossStreet': 'at W 50th St', 'lat': 40.759850056828405, 'lng': -73.97934397752239, 'labeledLatLngs': [{'label': 'display', 'lat': 40.759850056828405, 'lng': -73.97934397752239}], 'distance': 103, 'postalCode': '10020', 'cc': 'US', 'city': 'New York', 'state': 'NY', 'country': 'United States', 'formattedAddress': ['1260 Avenue of the Americas (at W 50th St)', 'New York, NY 10020', 'United States']}, 'categories': [{'id': '5032792091d4c4b30a586d5c', 'name': 'Concert Hall', 'pluralName': 'Concert Halls', 'shortName': 'Concert Hall', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/arts_entertainment/musicvenue_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}, 'venuePage': {'id': '348456

In [ ]:
NY_venues

Neighborhood  ...          Venue Category
0     Midtown Manhattan  ...            Concert Hall
1     Midtown Manhattan  ...                     Gym
2     Midtown Manhattan  ...              Art Museum
3     Midtown Manhattan  ...                   Plaza
4     Midtown Manhattan  ...              Art Museum
...                 ...  ...                     ...
3727       Forest Hills  ...          Clothing Store
3728       Forest Hills  ...      Salon / Barbershop
3729       Forest Hills  ...      Mexican Restaurant
3730       Forest Hills  ...      Chinese Restaurant
3731       Forest Hills  ...  Furniture / Home Store

[3732 rows x 7 columns]

In [ ]:
NY_venues.head()


Neighborhood  Neighborhood Latitude  ...  Venue Longitude Venue Category
0  Midtown Manhattan              40.760109  ...       -73.979344   Concert Hall
1  Midtown Manhattan              40.760109  ...       -73.977784            Gym
2  Midtown Manhattan              40.760109  ...       -73.976732     Art Museum
3  Midtown Manhattan              40.760109  ...       -73.978730          Plaza
4  Midtown Manhattan              40.760109  ...       -73.977462     Art Museum

[5 rows x 7 columns]

In [ ]:
NY_venues_count = NY_venues.groupby('Neighborhood').count().reset_index()
NY_venues_count[['Neighborhood', 'Venue']]


Neighborhood  Venue
0                Astoria     84
1      Battery Park City     92
2              Bay Ridge     27
3     Bedford-Stuyvesant     55
4            Boerum Hill     82
5       Brooklyn Heights    100
6               Bushwick     11
7        Carroll Gardens     98
8                Chelsea     45
9              Chinatown    100
10           Cobble Hill     88
11         Crown Heights     25
12                 Dumbo     87
13           East Harlem     43
14          East Village    100
15    Financial District    100
16     Flatiron District    100
17              Flushing     88
18          Forest Hills     43
19           Fort Greene     49
20      Garment District     78
21         Gramercy Park    100
22            Greenpoint     76
23     Greenwich Village    100
24                Harlem    100
25        Hell's Kitchen    100
26                Inwood      6
27       Jackson Heights     40
28          Little Italy    100
29      Long Island City    164
30       Lower East Side    100
31       Lower Manhattan     17
32  Meatpacking District    100
33          Midtown East    100
34     Midtown Manhattan     83
35   Morningside Heights     44
36           Murray Hill      2
37                Nolita    100
38            Park Slope     71
39      Prospect Heights      9
40              Red Hook     37
41                  SoHo    100
42           Sunset Park     42
43      Theater District    100
44               Tribeca    100
45          Union Square    100
46       Upper East Side     82
47       Upper Manhattan     16
48       Upper West Side     92
49    Washington Heights     44
50          West Village    100
51          Williamsburg     12

In [ ]:
print('So {} uniques categories.'.format(len(NY_venues['Venue Category'].unique())))

So 335 uniques categories.


### There are 335 uniques venues.

## Onehot Encoding

In [ ]:
NY_onehot = pd.get_dummies(NY_venues[['Venue Category']], prefix="", prefix_sep="") 

# add neighborhood column back to dataframe
NY_onehot['Neighborhood'] = NY_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [NY_onehot.columns[-1]] + list(NY_onehot.columns[:-1])
NY_onehot = NY_onehot[fixed_columns]

NY_onehot.head()

Yoga Studio  ATM  Accessories Store  ...  Wine Shop  Wings Joint  Women's Store
0            0    0                  0  ...          0            0              0
1            0    0                  0  ...          0            0              0
2            0    0                  0  ...          0            0              0
3            0    0                  0  ...          0            0              0
4            0    0                  0  ...          0            0              0

[5 rows x 335 columns]

In [ ]:
NY_grouped = NY_onehot.groupby('Neighborhood').mean().reset_index()
NY_grouped

Neighborhood  Yoga Studio  ...  Wings Joint  Women's Store
0                Astoria     0.000000  ...     0.000000       0.000000
1      Battery Park City     0.000000  ...     0.000000       0.000000
2              Bay Ridge     0.000000  ...     0.000000       0.000000
3     Bedford-Stuyvesant     0.000000  ...     0.000000       0.000000
4            Boerum Hill     0.024390  ...     0.000000       0.000000
5       Brooklyn Heights     0.040000  ...     0.000000       0.010000
6               Bushwick     0.000000  ...     0.000000       0.000000
7        Carroll Gardens     0.010204  ...     0.010204       0.000000
8                Chelsea     0.000000  ...     0.000000       0.022222
9              Chinatown     0.010000  ...     0.000000       0.000000
10           Cobble Hill     0.034091  ...     0.000000       0.000000
11         Crown Heights     0.000000  ...     0.000000       0.000000
12                 Dumbo     0.022989  ...     0.000000       0.000000
13           East Harlem     0.000000  ...     0.000000       0.000000
14          East Village     0.000000  ...     0.000000       0.000000
15    Financial District     0.010000  ...     0.000000       0.010000
16     Flatiron District     0.010000  ...     0.000000       0.000000
17              Flushing     0.000000  ...     0.000000       0.000000
18          Forest Hills     0.000000  ...     0.046512       0.000000
19           Fort Greene     0.000000  ...     0.000000       0.000000
20      Garment District     0.000000  ...     0.000000       0.000000
21         Gramercy Park     0.010000  ...     0.000000       0.000000
22            Greenpoint     0.052632  ...     0.000000       0.000000
23     Greenwich Village     0.010000  ...     0.000000       0.000000
24                Harlem     0.010000  ...     0.010000       0.010000
25        Hell's Kitchen     0.000000  ...     0.000000       0.000000
26                Inwood     0.000000  ...     0.000000       0.000000
27       Jackson Heights     0.000000  ...     0.000000       0.000000
28          Little Italy     0.010000  ...     0.000000       0.010000
29      Long Island City     0.024390  ...     0.000000       0.000000
30       Lower East Side     0.000000  ...     0.000000       0.010000
31       Lower Manhattan     0.000000  ...     0.000000       0.000000
32  Meatpacking District     0.000000  ...     0.000000       0.030000
33          Midtown East     0.000000  ...     0.000000       0.010000
34     Midtown Manhattan     0.000000  ...     0.000000       0.012048
35   Morningside Heights     0.000000  ...     0.000000       0.000000
36           Murray Hill     0.000000  ...     0.000000       0.000000
37                Nolita     0.000000  ...     0.000000       0.000000
38            Park Slope     0.000000  ...     0.000000       0.000000
39      Prospect Heights     0.000000  ...     0.000000       0.000000
40              Red Hook     0.000000  ...     0.000000       0.000000
41                  SoHo     0.000000  ...     0.000000       0.000000
42           Sunset Park     0.000000  ...     0.000000       0.023810
43      Theater District     0.000000  ...     0.000000       0.010000
44               Tribeca     0.000000  ...     0.010000       0.000000
45          Union Square     0.040000  ...     0.000000       0.020000
46       Upper East Side     0.000000  ...     0.000000       0.024390
47       Upper Manhattan     0.000000  ...     0.000000       0.000000
48       Upper West Side     0.010870  ...     0.000000       0.000000
49    Washington Heights     0.000000  ...     0.000000       0.000000
50          West Village     0.000000  ...     0.000000       0.000000
51          Williamsburg     0.000000  ...     0.000000       0.000000

[52 rows x 335 columns]

In [ ]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]


In [ ]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = NY_grouped['Neighborhood']

for ind in np.arange(NY_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(NY_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood  ...           10th Most Common Venue
0                Astoria  ...               Chinese Restaurant
1      Battery Park City  ...                   Sandwich Place
2              Bay Ridge  ...                        Nightclub
3     Bedford-Stuyvesant  ...             Caribbean Restaurant
4            Boerum Hill  ...             Gym / Fitness Center
5       Brooklyn Heights  ...                              Bar
6               Bushwick  ...                    Burrito Place
7        Carroll Gardens  ...                  Thai Restaurant
8                Chelsea  ...                      Supermarket
9              Chinatown  ...                     Cocktail Bar
10           Cobble Hill  ...                Food & Drink Shop
11         Crown Heights  ...              Fried Chicken Joint
12                 Dumbo  ...                              Gym
13           East Harlem  ...                French Restaurant
14          East Village  ...                     Dessert Shop
15    Financial District  ...                      Event Space
16     Flatiron District  ...                     Cycle Studio
17              Flushing  ...                       Bath House
18          Forest Hills  ...                   Shipping Store
19           Fort Greene  ...  Southern / Soul Food Restaurant
20      Garment District  ...             Fast Food Restaurant
21         Gramercy Park  ...                       Bagel Shop
22            Greenpoint  ...                    Deli / Bodega
23     Greenwich Village  ...                Indian Restaurant
24                Harlem  ...                       Kids Store
25        Hell's Kitchen  ...                    Indie Theater
26                Inwood  ...             Ethiopian Restaurant
27       Jackson Heights  ...                       Donut Shop
28          Little Italy  ...                  Bubble Tea Shop
29      Long Island City  ...                             Park
30       Lower East Side  ...                      Art Gallery
31       Lower Manhattan  ...                     Burger Joint
32  Meatpacking District  ...                             Café
33          Midtown East  ...               Mexican Restaurant
34     Midtown Manhattan  ...              Lebanese Restaurant
35   Morningside Heights  ...                College Cafeteria
36           Murray Hill  ...                          Exhibit
37                Nolita  ...                     Burger Joint
38            Park Slope  ...                           Bakery
39      Prospect Heights  ...                    Women's Store
40              Red Hook  ...                        Bookstore
41                  SoHo  ...                   Chocolate Shop
42           Sunset Park  ...                    Deli / Bodega
43      Theater District  ...                        Bookstore
44               Tribeca  ...               Italian Restaurant
45          Union Square  ...          New American Restaurant
46       Upper East Side  ...                        Gift Shop
47       Upper Manhattan  ...                   Cosmetics Shop
48       Upper West Side  ...                       Bagel Shop
49    Washington Heights  ...                  Bubble Tea Shop
50          West Village  ...                      Coffee Shop
51          Williamsburg  ...              American Restaurant

[52 rows x 11 columns]

## Running Clusttering Algorithum

In [ ]:
kclusters = 4

NY_grouped_clustering = NY_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(NY_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[:] 


array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 3], dtype=int32)

In [ ]:
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

NY_merged = NY_neighborhood

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
NY_merged = NY_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

NY_merged.head() # check the last columns!
NY_merged = NY_merged.dropna()

In [ ]:

map_clusters = folium.Map(location=[latitude_NY, longitude_NY], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(NY_merged['Latitude'], NY_merged['Longitude'], NY_merged['Neighborhood'], NY_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [ ]:
print("Cluster 1")
NY_merged.loc[NY_merged['Cluster Labels'] == 0, NY_merged.columns[[0] + list(range(4, NY_merged.shape[1]))]]


Cluster 1


Neighborhood  ...           10th Most Common Venue
0      Midtown Manhattan  ...              Lebanese Restaurant
1                   SoHo  ...                   Chocolate Shop
2                 Harlem  ...                       Kids Store
3        Upper East Side  ...                        Gift Shop
4                Tribeca  ...               Italian Restaurant
5        Upper West Side  ...                       Bagel Shop
7        Lower East Side  ...                      Art Gallery
8        Lower Manhattan  ...                     Burger Joint
9      Greenwich Village  ...                Indian Restaurant
10          East Village  ...                     Dessert Shop
11          Little Italy  ...                  Bubble Tea Shop
12    Financial District  ...                      Event Space
13             Chinatown  ...                     Cocktail Bar
14        Hell's Kitchen  ...                    Indie Theater
15                 Dumbo  ...                              Gym
16               Chelsea  ...                      Supermarket
17     Flatiron District  ...                     Cycle Studio
18               Astoria  ...               Chinese Restaurant
19            Park Slope  ...                           Bakery
20                Nolita  ...                     Burger Joint
21         Gramercy Park  ...                       Bagel Shop
22            Greenpoint  ...                    Deli / Bodega
23      Long Island City  ...                             Park
24  Meatpacking District  ...                             Café
25      Brooklyn Heights  ...                              Bar
26          Midtown East  ...               Mexican Restaurant
27      Theater District  ...                        Bookstore
29    Washington Heights  ...                  Bubble Tea Shop
30          West Village  ...                      Coffee Shop
31          Union Square  ...          New American Restaurant
32              Bushwick  ...                    Burrito Place
33     Battery Park City  ...                   Sandwich Place
34    Bedford-Stuyvesant  ...             Caribbean Restaurant
35           East Harlem  ...                French Restaurant
36              Flushing  ...                       Bath House
37      Prospect Heights  ...                    Women's Store
39       Carroll Gardens  ...                  Thai Restaurant
40       Jackson Heights  ...                       Donut Shop
41           Fort Greene  ...  Southern / Soul Food Restaurant
42             Bay Ridge  ...                        Nightclub
43           Boerum Hill  ...             Gym / Fitness Center
44              Red Hook  ...                        Bookstore
45           Sunset Park  ...                    Deli / Bodega
46      Garment District  ...             Fast Food Restaurant
47           Cobble Hill  ...                Food & Drink Shop
48       Upper Manhattan  ...                   Cosmetics Shop
49   Morningside Heights  ...                College Cafeteria
50         Crown Heights  ...              Fried Chicken Joint
51              Flushing  ...                       Bath House
52               Astoria  ...               Chinese Restaurant
53      Long Island City  ...                             Park
54          Forest Hills  ...                   Shipping Store

[52 rows x 11 columns]

In [ ]:
print("Cluster 2")
NY_merged.loc[NY_merged['Cluster Labels'] == 1, NY_merged.columns[[0] + list(range(4, NY_merged.shape[1]))]]


Cluster 2


Neighborhood  ... 10th Most Common Venue
38       Inwood  ...   Ethiopian Restaurant

[1 rows x 11 columns]

In [ ]:
print("Cluster 3")
NY_merged.loc[NY_merged['Cluster Labels'] == 2, NY_merged.columns[[0] + list(range(4, NY_merged.shape[1]))]]


Cluster 3


Neighborhood  ... 10th Most Common Venue
35     Flushing  ...      Fish & Chips Shop

[1 rows x 11 columns]

In [ ]:
print("Cluster 4")
NY_merged.loc[NY_merged['Cluster Labels'] == 3, NY_merged.columns[[0] + list(range(4, NY_merged.shape[1]))]]


Cluster 4


Neighborhood  ... 10th Most Common Venue
6  Williamsburg  ...    American Restaurant

[1 rows x 11 columns]

# Conclusion:
After doing the K means clustering and other analysis described in the python notebook we are of the Opinion that the person should reside in Cluster 1. This is because the person wants to live in a happening place nearby. Cluster one has all the facilities the client is looking for. 
